#### Importing required libraries

In [1]:
import pymongo
import pandas as pd

#### Connect to MongoDB

In [2]:
client = pymongo.MongoClient("mongodb://localhost:27017/")
database_name = "spotify_recommendations"
db = client[database_name]

#### Load Dataset into MongoDB

In [3]:
# Load CSV dataset into a Pandas DataFrame
csv_file_path = "spotify_dataset.csv"
df = pd.read_csv(csv_file_path)

# Convert DataFrame to a list of dictionaries for MongoDB insertion
data = df.to_dict(orient='records')

# Create a collection and insert data into MongoDB
collection_name = "tracks"
collection = db[collection_name]
collection.insert_many(data)

InsertManyResult([ObjectId('6587b1a6ade84a250b01a4ef'), ObjectId('6587b1a6ade84a250b01a4f0'), ObjectId('6587b1a6ade84a250b01a4f1'), ObjectId('6587b1a6ade84a250b01a4f2'), ObjectId('6587b1a6ade84a250b01a4f3'), ObjectId('6587b1a6ade84a250b01a4f4'), ObjectId('6587b1a6ade84a250b01a4f5'), ObjectId('6587b1a6ade84a250b01a4f6'), ObjectId('6587b1a6ade84a250b01a4f7'), ObjectId('6587b1a6ade84a250b01a4f8'), ObjectId('6587b1a6ade84a250b01a4f9'), ObjectId('6587b1a6ade84a250b01a4fa'), ObjectId('6587b1a6ade84a250b01a4fb'), ObjectId('6587b1a6ade84a250b01a4fc'), ObjectId('6587b1a6ade84a250b01a4fd'), ObjectId('6587b1a6ade84a250b01a4fe'), ObjectId('6587b1a6ade84a250b01a4ff'), ObjectId('6587b1a6ade84a250b01a500'), ObjectId('6587b1a6ade84a250b01a501'), ObjectId('6587b1a6ade84a250b01a502'), ObjectId('6587b1a6ade84a250b01a503'), ObjectId('6587b1a6ade84a250b01a504'), ObjectId('6587b1a6ade84a250b01a505'), ObjectId('6587b1a6ade84a250b01a506'), ObjectId('6587b1a6ade84a250b01a507'), ObjectId('6587b1a6ade84a250b01a5

####  Execute Read/Write Queries

**1. Query to Retrieve Track Recommendations Based on Genre**

In [4]:
# User's current track details
current_track_id = "5SuOikwiRyPMVoIQDJUgSV"
current_track_genre = "acoustic"

# Query to get recommended tracks based on the same genre
collection = db.get_collection(name="tracks", read_concern=pymongo.read_concern.ReadConcern("majority"))
recommended_tracks = collection.find(
    {"track_genre": current_track_genre, "track_id": {"$ne": current_track_id}},
    {"_id": 0, "track_id": 1, "track_name": 1, "artists": 1, "track_genre": 1}
).limit(5)

# Print recommended tracks
for track in recommended_tracks:
    print(track)

{'track_id': '4qPNDBW1i3p13qLCt0Ki3A', 'artists': 'Ben Woodward', 'track_name': 'Ghost - Acoustic', 'track_genre': 'acoustic'}
{'track_id': '1iJBSr7s7jYXzM8EGcbK5b', 'artists': 'Ingrid Michaelson;ZAYN', 'track_name': 'To Begin Again', 'track_genre': 'acoustic'}
{'track_id': '6lfxq3CG4xtTiEg7opyCyx', 'artists': 'Kina Grannis', 'track_name': "Can't Help Falling In Love", 'track_genre': 'acoustic'}
{'track_id': '5vjLSffimiIP26QG5WcN2K', 'artists': 'Chord Overstreet', 'track_name': 'Hold On', 'track_genre': 'acoustic'}
{'track_id': '01MVOl9KtVTNfFiBU9I7dc', 'artists': 'Tyrone Wells', 'track_name': 'Days I Will Remember', 'track_genre': 'acoustic'}


**2. Query to Retrieve Tracks with High Danceability:**

In [5]:
# Query to get tracks with high danceability
high_danceability_tracks = collection.find(
    {"danceability": {"$gt": 0.8}},
    {"_id": 0, "track_name": 1, "artists": 1, "danceability": 1}
).limit(5)

# Print high danceability tracks
for track in high_danceability_tracks:
    print(track)


{'artists': 'Zee Avi', 'track_name': 'No Christmas For Me', 'danceability': 0.809}
{'artists': 'Us The Duo', 'track_name': 'Shotgun', 'danceability': 0.806}
{'artists': 'Andrew Foy;Renee Foy', 'track_name': 'Photograph', 'danceability': 0.807}
{'artists': 'Gen Hoshino', 'track_name': 'I Wanna Be Your Ghost (feat. Ghosts)', 'danceability': 0.829}
{'artists': 'Tyrone Wells', 'track_name': 'Days I Will Remember', 'danceability': 0.804}


**3. Query to Retrieve Tracks with Similar Energy and Valence**

In [6]:
# User's current track details
current_track_energy = 0.7
current_track_valence = 0.8

# Query to get tracks with similar energy and valence
collection = db.get_collection("tracks", write_concern=pymongo.write_concern.WriteConcern("majority"))
similar_tracks = collection.find(
    {"energy": {"$gte": current_track_energy - 0.1, "$lte": current_track_energy + 0.1},
     "valence": {"$gte": current_track_valence - 0.1, "$lte": current_track_valence + 0.1}},
    {"_id": 0, "track_name": 1, "artists": 1, "energy": 1, "valence": 1}
).limit(5)

# Print similar tracks
for track in similar_tracks:
    print(track)


{'artists': 'Jason Mraz', 'track_name': 'Unlonely', 'energy': 0.667, 'valence': 0.754}
{'artists': 'Brandi Carlile;Lucius', 'track_name': 'You and Me on the Rock', 'energy': 0.686, 'valence': 0.725}
{'artists': 'Brandi Carlile;Lucius', 'track_name': 'You and Me on the Rock', 'energy': 0.686, 'valence': 0.725}
{'artists': 'Brandi Carlile;Lucius', 'track_name': 'You and Me on the Rock', 'energy': 0.686, 'valence': 0.725}
{'artists': 'Brandi Carlile;Lucius', 'track_name': 'You and Me on the Rock', 'energy': 0.686, 'valence': 0.725}
